In [49]:
from utils.db import dbconn
conn = dbconn('dawndb')
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format
df_rates = pd.read_sql_query("SELECT date, rate FROM rates where name='FED_FUND'",
                             conn,
                             parse_dates=['date'],
                             index_col=['date']).sort_index()
df_balances = pd.read_sql_query("SELECT * FROM strategy_im",
                                conn,
                                parse_dates=['date'],
                                index_col=['date']).sort_index()
df_balances[['broker', 'strategy']] = df_balances[['broker', 'strategy']].astype('category')

In [104]:
from IPython.display import display
from pandas.tseries.offsets import BDay
import numpy as np

def f(df_balances, df_rates, broker, start_date, end_date):
    df = (df_balances[df_balances.broker == broker].
      set_index("strategy", append=True)["amount"].
      unstack("strategy"))
    df[df.isnull()] = 0.
    drange = pd.date_range(pd.Timestamp(start_date) - BDay(), end_date)
    rates = df_rates.reindex(drange, method="ffill") /100 /360
    df = df.reindex(drange, method="ffill")
    if broker in ["BAML_ISDA", "CITI"]:
        d = {}
        for strat in df:
            s = df.loc[start_date:, strat]
            ir_bal = 0.
            for bal, r in zip(s.values, rates.loc[start_date:, 'rate'].values):
                bal += ir_bal
                ir_bal += bal * r
            d[strat] = ir_bal
        result = pd.Series(d, name='amount')
    else:
        result = (df.loc[start_date:] * rates.loc[start_date:].values).sum().to_frame(name='amount')
    display(result)
    print(result.sum())
    
from functools import partial
f_print = partial(f, df_balances, df_rates)

In [105]:
from ipywidgets import widgets, Layout
import datetime
broker_widget = widgets.Dropdown(
    options=df_balances.broker.cat.categories,
    value='CITI',
    description='Broker:',
    disabled=False,
)
start_date = widgets.DatePicker(
    description='start:',
    disabled=False,
    value=datetime.date(2019, 9, 1)
)
end_date = widgets.DatePicker(
    description='end:',
    disabled=False,
    value=datetime.date(2019, 9, 30)
)
output = widgets.interactive_output(f_print, {'broker': broker_widget, 'start_date': start_date, 'end_date': end_date})
output.layout= Layout(margin='auto auto auto 90px')
widgets.VBox([widgets.HBox([broker_widget, start_date, end_date]), output])

In [ ]:
df_balances[df_balances.broker=='BAML_ISDA'].loc["2019-06-10"]

In [106]:
df_baml=df_balances[df_balances.broker == "BAML_ISDA"]
df_baml.groupby(df_baml.index)['amount'].sum()["2019-08-30":]

date
2019-08-30   -910,332.93
2019-09-02   -910,332.93
2019-09-03   -910,332.93
2019-09-04   -911,899.69
2019-09-05   -911,899.69
2019-09-06   -911,899.69
2019-09-09   -911,899.69
2019-09-10   -911,899.69
2019-09-11   -911,899.69
2019-09-12   -911,899.69
2019-09-13   -911,899.69
2019-09-16   -911,899.69
2019-09-17   -911,899.69
2019-09-18   -911,899.69
2019-09-19   -911,899.69
2019-09-20   -911,899.69
2019-09-23   -911,899.69
2019-09-24   -911,899.69
2019-09-25   -911,899.69
2019-09-26   -911,899.69
2019-09-27   -911,899.69
2019-09-30   -911,899.69
2019-10-01   -911,899.69
2019-10-02   -913,453.48
2019-10-03   -913,453.48
2019-10-04   -913,453.48
2019-10-07   -913,453.48
Name: amount, dtype: float64